In [ ]:
#配置参数
import argparse
parser = argparse.ArgumentParser()#创建一个对象 下面是设置各种参数
parser.add_argument("--epochs", type=int, default=20, help="number of epochs of training")
parser.add_argument("--batch_size", type=int, default=64, help="size of the batches")
parser.add_argument("--lr", type=float, default=0.0002, help="learning rate")
parser.add_argument("--latent_dim", type=int, default=100, help="dimensionality of the latent space")
parser.add_argument("--sample_interval", type=int, default=100, help="interval between image samples")
opt = parser.parse_args(args=[]) #这里貌似在在jupyter notebook中,args不应为空

In [2]:
#面部图片Dataset
import os
from PIL import Image
from torch.utils.data import Dataset,DataLoader
class Face(Dataset):
    def __init__(self, root, transforms=None):
        imgs = os.listdir(root) #这里存的不是所有图片，是图片的路径，在调用__getitem__的时候才会加载图片
        self.imgs = [os.path.join(root,img) for img in imgs] #路径拼接

        self.transforms = transforms #对图片进行一些调整操作

    def __len__(self):
        return len(self.imgs)

    def __getitem__(self, idx):
        img_path = self.imgs[idx] #根据路径返回图片
        data = Image.open(img_path)
        if self.transforms:
            data=self.transforms(data)
        return data

c:\Users\24508\Anaconda3\envs\jqxx\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
ngf = 64 #生成器中的特征图大小
nz = 100 #生成器输入的尺寸
#生成器网络，接收随机噪声作为输入，生成逼真的图像。
import torch.nn as nn
class Generator(nn.Module):
    def __init__(self):
        super().__init__()

        #输入大小为nz * 1 * 1
        self.model = nn.Sequential(
            nn.ConvTranspose2d(nz, ngf * 8, 4, 1, 0, bias=False), #反卷积层，#前5个参数分别是输入通道数，输出通道数，卷积核大小，卷积核每次移动多少个像素，原图片边缘加几个空白像素，输出边缘加几个空白像素
            nn.BatchNorm2d(ngf * 8), #百度的：进行数据归一化处理，使数据在Relu之前不会因为数据过大导致网络性能不稳定
            nn.ReLU(inplace=True),  #ReLU激活函数
            # 输出大小为(ngf*8) x 4 x 4 。这里有个计算公式 输出尺寸 = (输入尺寸 - 1) * 步长 + 卷积核大小 - 2*输入填充 + 输出填充

            nn.ConvTranspose2d(ngf * 8, ngf * 4, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(ngf * 4),
            nn.ReLU(inplace=True),
            # 输出大小为(ngf*4) x 8 x 8

            nn.ConvTranspose2d(ngf * 4, ngf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 2), 
            nn.ReLU(inplace=True), 
            # 输出大小为(ngf*2) x 16 x 16

            nn.ConvTranspose2d(ngf * 2, ngf , 4, 2, 1, bias=False), 
            nn.BatchNorm2d(ngf),
            nn.ReLU(inplace=True),
            # 输出大小为(ngf) x 32 x 32

            nn.ConvTranspose2d(ngf, 3 , 4, 2, 1, bias=False), 
            nn.Tanh()  #Tanh激活函数
            # 输出大小为(ngf) x 64 x 64
        )
    def forward(self, z): #输入随机噪声z
        img = self.model(z)
        img = img.reshape(img.size(0), 3, 64, 64) #强制调整尺寸，加上第一维
        return img

In [4]:
ndf = 64 #通道数，这里设置的有点大有待研究
#判别器网络，尝试区分真实的图像和生成器生成的图像
class Discriminator(nn.Module):
    def __init__(self):
        super().__init__()

        #输入大小为3 * 64 * 64
        self.model = nn.Sequential( #Sequential是一个模块容器，用了这个就不用再写一遍向前传播了 
            nn.Conv2d(3, ndf, 4, 2, 1, bias=False), #前5个参数分别是输入通道数，输出通道数，卷积核大小，卷积核每次移动多少个像素，原图片边缘加几个空白像素
            nn.LeakyReLU(0.2, inplace=True), #激活函数,inplace=True直接修改原数据
            #输出大小为 (ndf) * 32 * 32 。这里有个计算公式 输出尺寸 = (输入尺寸 + 2*填充 - 卷积核大小) / 步长 + 1，除法是向下取整

            nn.Conv2d(ndf, ndf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 2), #百度的：进行数据归一化处理，使数据在Relu之前不会因为数据过大导致网络性能不稳定
            nn.LeakyReLU(0.2, inplace=True),
            #输出大小为 (ndf*2) * 16 * 16

            nn.Conv2d(ndf * 2, ndf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 4), 
            nn.LeakyReLU(0.2, inplace=True),
            #输出大小为  (ndf*4) * 8 * 8

            nn.Conv2d(ndf * 4, ndf * 8, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 8),
            nn.LeakyReLU(0.2, inplace=True),
            #输出大小为 (ndf*8) * 4 * 4

            nn.Conv2d(ndf * 8, 1, 4, 1, 0, bias=False),
            nn.Sigmoid() #激活函数，输出0到1之间的概率
        )
    def forward(self, img):
        return self.model(img)

In [5]:
#加载数据集

import torchvision.transforms as transforms
tfm=transforms.Compose([
                           transforms.Resize(64), #保持原始宽高比进行等比缩放，将图像的较短边调整到64像素
                           transforms.CenterCrop(64), #从图像中心裁剪出64×64像素的区域
                           transforms.ToTensor(), #转换为PyTorch张量
                           transforms.Normalize((0.5, 0.5, 0.5), #将值范围从[0,1]变换到[-1,1]，第一个为RGB三个通道的均值，第二个为标准差
                                                (0.5, 0.5, 0.5)),
                           ])
FaceData = Face('./img_align_celeba', transforms=tfm)
data_loader = DataLoader(FaceData,batch_size=opt.batch_size,shuffle=True)#数据读取

In [6]:
import torch
import numpy as np
from torchvision.utils import save_image


if __name__ == '__main__':
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")#设备
    Tensor = torch.cuda.FloatTensor if torch.cuda.is_available() else torch.FloatTensor
    print('当前device为' + str(device))

    generator = Generator().to(device) #生成器
    discriminator = Discriminator().to(device) #判别器
    adversarial_loss = torch.nn.BCELoss().to(device) #损失函数

    optimizer_G = torch.optim.Adam(generator.parameters(), lr=opt.lr ) #优化器
    optimizer_D = torch.optim.Adam(discriminator.parameters(), lr=opt.lr ) #优化器

    os.makedirs("generated-facial-images", exist_ok=True) #创建存储生成图片的目录，exist_ok=True就可以让文件夹存在的时候也不会报错

    #开始训练
    for epoch in range(opt.epochs):
        i=0
        for imgs in data_loader:
            i=i+1

            # 真实样本和假样本的标签，1代表真实图片，0代码生成网络生成的图片，valid:batch_sizex1的全1向量，fake:batch_sizex1的全零向量
            valid = torch.tensor(Tensor(imgs.size(0), 1,1,1).fill_(1.0), requires_grad=False) #requires_grad=False表示不需要计算梯度（不参与反向传播）
            fake = torch.tensor(Tensor(imgs.size(0), 1,1,1).fill_(0.0), requires_grad=False)

            #先搞生成器
            optimizer_G.zero_grad()
            z = torch.tensor(Tensor(np.random.normal(0, 1, (imgs.shape[0], opt.latent_dim,1,1)))) #z是有标准正态分布采样得到的batch_sizex100向量，100是生成器nz大小，也就是opt.latent_dim
            gen_imgs = generator(z) #生成图片,64x3x64x64
            g_loss = adversarial_loss(discriminator(gen_imgs), valid) #生成器损失函数：让生成的图像通过判别器后与valid相比较，越靠近越好
            g_loss.backward()
            optimizer_G.step()


            #再搞判别器
            optimizer_D.zero_grad()
            real_imgs = torch.tensor(imgs.type(Tensor))
            real_loss = adversarial_loss(discriminator(real_imgs), valid) #判别器损失函数：一方面让真实图片通过判别器与valid越接近，另一方面让生成的图片通过判别器与fake越接近(正好与生成器相矛盾，这样才能提高判别能力)
            fake_loss = adversarial_loss(discriminator(gen_imgs.detach()), fake)
            d_loss = (real_loss + fake_loss) / 2
            d_loss.backward()
            optimizer_D.step()

            #输出信息
            print(
                "[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f]"
                % (epoch, opt.epochs, i, len(data_loader), d_loss.item(), g_loss.item())
            )

            #每隔一段保存一下图片
            batches_done = epoch * len(data_loader) + i
            if batches_done % opt.sample_interval == 0:
                save_image(gen_imgs.data[:25], "generated-facial-images/%d.png" % batches_done, nrow=5, normalize=True)

当前device为cuda


c:\Users\24508\Anaconda3\envs\jqxx\lib\site-packages\ipykernel_launcher.py:27: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
c:\Users\24508\Anaconda3\envs\jqxx\lib\site-packages\ipykernel_launcher.py:28: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
c:\Users\24508\Anaconda3\envs\jqxx\lib\site-packages\ipykernel_launcher.py:32: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
c:\Users\24508\Anaconda3\envs\jqxx\lib\site-packages\ipykernel_launcher.py:41: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().deta

[Epoch 0/20] [Batch 1/3166] [D loss: 0.718379] [G loss: 0.563639]
[Epoch 0/20] [Batch 2/3166] [D loss: 0.231244] [G loss: 1.357146]
[Epoch 0/20] [Batch 3/3166] [D loss: 0.082824] [G loss: 2.441263]
[Epoch 0/20] [Batch 4/3166] [D loss: 0.081259] [G loss: 2.578156]
[Epoch 0/20] [Batch 5/3166] [D loss: 0.092634] [G loss: 2.172273]
[Epoch 0/20] [Batch 6/3166] [D loss: 0.097003] [G loss: 1.970682]
[Epoch 0/20] [Batch 7/3166] [D loss: 0.076774] [G loss: 2.514474]
[Epoch 0/20] [Batch 8/3166] [D loss: 0.134521] [G loss: 3.092866]
[Epoch 0/20] [Batch 9/3166] [D loss: 0.077692] [G loss: 2.758557]
[Epoch 0/20] [Batch 10/3166] [D loss: 0.114320] [G loss: 2.772839]
[Epoch 0/20] [Batch 11/3166] [D loss: 0.037609] [G loss: 3.387866]
[Epoch 0/20] [Batch 12/3166] [D loss: 0.106584] [G loss: 4.094378]
[Epoch 0/20] [Batch 13/3166] [D loss: 0.077118] [G loss: 3.370970]
[Epoch 0/20] [Batch 14/3166] [D loss: 0.047476] [G loss: 3.365112]
[Epoch 0/20] [Batch 15/3166] [D loss: 0.036970] [G loss: 3.790543]
[Epo